In [5]:
"""
An ant moves on a regular grid of squares that are coloured either black or white.
The ant is always oriented in one of the cardinal directions (left, right, up or down) and moves from square to adjacent square according to the following rules:
- if it is on a black square, it flips the color of the square to white, rotates 90 degrees counterclockwise and moves forward one square.
- if it is on a white square, it flips the color of the square to black, rotates 90 degrees clockwise and moves forward one square.

Starting with a grid that is entirely white, how many squares are black after 10^18 moves of the ant?
"""
import numpy as np
import math
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import BoxAnnotation
from bokeh.charts import Step
output_notebook()

dim = 330
field = np.zeros((dim,dim), dtype=np.int)
black_tiles_per_step = list()
white = 0
black = 1
#print(field)
start_position = np.array([dim//2,dim//2])
looking_direction = np.array([1,0])
clockwise = -2*math.pi / 4
counterclockwise = -clockwise
def get_rotation_matrix(angle):
    return np.array([[math.cos(angle), -math.sin(angle)], 
                     [math.sin(angle),  math.cos(angle)]]).astype(int)
rotation_matrix_clockwise = get_rotation_matrix(clockwise)
rotation_matrix_counterclockwise = get_rotation_matrix(counterclockwise)
# print(rotation_matrix_clockwise, rotation_matrix_counterclockwise) 
def color_of_position(position):
    return field[position[0], position[1]]

def flip(position):
    field[position[0], position[1]] =  not field[position[0], position[1]] # flips bit
    
def move(position, looking_direction):
    flip(position)
    if color_of_position(position) == white:        
        looking_direction = rotation_matrix_clockwise.dot(looking_direction)
    else:           
        looking_direction = rotation_matrix_counterclockwise.dot(looking_direction)
    return position + looking_direction, looking_direction

def print_field(field, position, looking_direction):
  
    def hex_to_rgb(value):
        value = value.lstrip('#')
        lv = len(value)
        return tuple(int(value[i:i + lv // 3], 16) for i in range(0, lv, lv // 3))

    def rgb_to_hex(rgb):
        return '#%02x%02x%02x' % rgb
    
    red = "#C63D0F"
    black = "#3B3738"
    white = "#FDF3E7"
    green = "#7E8F7C"

    N = dim
    
    img = field.copy()
    view = img.view(dtype=np.uint8).reshape((N, N, 4))
    for i in range(N):
        for j in range(N):
            if field[i,j] == True:
                color = hex_to_rgb(black)
            else:
                color = hex_to_rgb(white)
            if np.array_equal(position, np.array([i,j])):
                color = hex_to_rgb(red)
            if np.array_equal((position + looking_direction), np.array([i,j])):
                color = hex_to_rgb(green)                
            view[i, j, 0] = color[0]
            view[i, j, 1] = color[1]
            view[i, j, 2] = color[2]
            view[i, j, 3] = 255

    output_file("image_rgba.html", title="image_rgba.py example")
    
    p = figure(x_range=[0,N], y_range=[0,N])
    p.image_rgba(image=[img], x=[0], y=[0], dw=[N], dh=[N])

    show(p)  # open a browser
    
    
def print_list(list_):
    TOOLS = "pan,wheel_zoom,box_zoom,reset,save,box_select"   
    
    """
    p1 = figure(title="Black tiles per step", tools=TOOLS)
    x = []
    for i in range(len(list_)):
        x.append(i)
        
    p1.circle(x, list_, legend="black", line_color="green")        
    p1.line(x, list_, legend="black", line_color="green")
    mid_box = BoxAnnotation(plot=p1, right=10100, fill_alpha=0.1, fill_color='green')
    p1.renderers.extend([mid_box])
    show(p1)
    """
    xyvalues = list_
    chart = Step(xyvalues, title="steps", ylabel='black tiles')
    mid_box = BoxAnnotation(plot=chart, right=10100, fill_alpha=0.1, fill_color='green')
    chart.renderers.extend([mid_box])
    show(chart)
    
def count_tiles(field):
    return np.sum(field)

def steps(start_position, looking_direction, number_of_steps, print_every_step = False):
    position = start_position
    for i in range(number_of_steps):
        black_tiles_per_step.append(count_tiles(field))
        position, looking_direction = move(position, looking_direction)
        if not ((5 < position[0] < dim-5) and (5 < position[1] < dim-5)):
            print("running into boundary, breaking at step", i)
            break
        if False:
            print("position", position)
            print("looking", looking_direction)
            print(field)
        if print_every_step:
            print_field(field, position, looking_direction)  
    print("calculation done")        
    print("black tiles per step")
    print_list(black_tiles_per_step)
    print("as you can see, around 1100 steps there is a point where systematic progress happens")
    
    print_field(field, position, looking_direction)
            
#print("position", start_position)
#print("looking", looking_direction)
#print(field)
#print_field(field, start_position, looking_direction)            
steps(start_position, looking_direction, 40000, False) 

Loading BokehJS ...

running into boundary, breaking at step 17374
calculation done
black tiles per step


as you can see, around 1100 steps there is a point where systematic progress happens


NameError: name 'output_file' is not defined

In [4]:
# use autocorrelation to find repetition rate / needed steps to repeat
def serial_corr(wave, lag=1):
    n = len(wave)
    y1 = wave[lag:]
    y2 = wave[:n-lag]
    corr = np.corrcoef(y1, y2, ddof=0)[0, 1]
    return corr
def autocorr(wave):
    lags = range(len(wave)//2)
    corrs = [serial_corr(wave, lag) for lag in lags]
    return lags, corrs

def print_random_list(list_):
    TOOLS = "pan,wheel_zoom,box_zoom,reset,save,box_select"   

    p1 = figure(title="list", tools=TOOLS)
    x = []
    for i in range(len(list_)):
        x.append(i)
        
    p1.circle(x, list_, legend="black", line_color="green")        
    p1.line(x, list_, legend="black", line_color="green")
    show(p1)

# after more than 10200 steps repetition begins, see plot
lags, corrs = autocorr(black_tiles_per_step[10200:])
print_random_list(corrs)
perfect_correlation = []
for i,c in enumerate(corrs):
    if c == 1.0:
        perfect_correlation.append(i)
minimum_repetition_faktor = perfect_correlation[1]        
print("perfect correclation after steps: ", minimum_repetition_faktor)        

perfect correclation after steps:  104


In [19]:
"""
we want to know 
black_tiles_per_step[10^18]
we know 
black_tiles_per_step[15000]
and that lets say 
black_tiles_per_step[15000+minimum_repetition_faktor] should be equal to 
== black_tiles_per_step[15000] + black_tiles_per_step[15000+minimum_repetition_faktor] - black_tiles_per_step[15000]
== black_tiles_per_step[15000] + black_tiles_per_step[15000+2*minimum_repetition_faktor] - black_tiles_per_step[15000+minimum_repetition_faktor]
== black_tiles_per_step[15000] + black_tiles_per_step[15000+n*minimum_repetition_faktor] - black_tiles_per_step[15000+(n-1)*minimum_repetition_faktor]
== black_tiles_per_step[15000] + (black_tiles_per_step[15000+minimum_repetition_faktor] - black_tiles_per_step[15000])
lets test that:
"""
# print(black_tiles_per_step[15000+minimum_repetition_faktor] == black_tiles_per_step[15000] + (black_tiles_per_step[15000+minimum_repetition_faktor] - black_tiles_per_step[15000]))
    
"""
lets invent some backtracking.
Lets say I want to know black_tiles_per_step[x]
"""
def predict_black_tiles_per_step(black_tiles_per_step, minimum_repetition_faktor, step):
    baseline = 15000
    x_remaining = x - baseline
    n = x_remaining // minimum_repetition_faktor
    fillup = x_remaining % minimum_repetition_faktor
    baseline = baseline + fillup
    return black_tiles_per_step[baseline] + n*(black_tiles_per_step[15000+minimum_repetition_faktor] - black_tiles_per_step[15000])
    
x = 17000
for x in range(16500, 16500+2*minimum_repetition_faktor):    
    # test if prediction matches direct calculation
    if not black_tiles_per_step[x] == predict_black_tiles_per_step(black_tiles_per_step, minimum_repetition_faktor, x):
        print("test failed")
        
x = 10**18        
print(predict_black_tiles_per_step(black_tiles_per_step, minimum_repetition_faktor, x))  

115384615384614952
